In [1]:
import torch
import transformers

print(torch.__version__)
transformers.__version__

D:\Anaconda3\envs\pytorch-gpu\lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


2.0.1


'4.30.2'

In [2]:
import json

data_path ="./CJRC/transfered/big_train_data.json"

with open(data_path, "r", encoding="utf-8") as f:
    data = json.load(f)["data"]
    len_train = len(data)
print(len_train)
del data

8000


In [88]:
# model

import torch
import torch.nn as nn
from transformers import BertTokenizer, BertConfig, BertForQuestionAnswering, BertModel
from transformers import InputExample
from transformers.data.processors.squad import SquadV2Processor, squad_convert_examples_to_features
from transformers.data.datasets.squad import SquadDataset

config = BertConfig.from_pretrained('bert-base-chinese')
# config = BertConfig.from_pretrained('chinese-bert-wwm')
print(config.hidden_size)
config.to_json_file("self_QA/config.json")
tokenizer = BertTokenizer.from_pretrained("bert-base-chinese", config=config)
# tokenizer = BertTokenizer.from_pretrained("chinese-bert-wwm", config=config)

768


In [70]:
import json
import torch
from torch.utils.data import Dataset

class MyDataset(Dataset):
    def __init__(self, data_path, mode='train'):
        
        with open(data_path, "r", encoding="utf-8") as f:
            self.data = json.load(f)["data"]
        self.samples = []
        self.long_samples = []  # 记录输入文本长度大于512的样本的索引
        for item in self.data:
            for paragraph in item["paragraphs"]:
                context = paragraph["context"]
                for qa in paragraph["qas"]:
                    question = qa["question"]
                    id = qa["id"]
                    if mode == 'train':
                        answer_start = [answer["answer_start"] for answer in qa["answers"]]
                        answer_text = [answer["text"] for answer in qa["answers"]]
                    else: # 验证集会有多个答案(不用这样也可以，不传入mode参数即可)
                        answer_start = [max(answer["answer_start"] for answer in qa["answers"])]
                        answer_text = [max(answer["text"] for answer in qa["answers"])]
                    if len(answer_start) == 0 or len(answer_text) == 0: # 如果答案为空，忽略该样本
                        continue
#                     input_dict = tokenizer.encode_plus(
#                         question, context, max_length=512, padding="max_length", truncation=True, return_tensors="pt"
#                     )
#                     if input_dict["input_ids"].shape[1] > 512:  # 如果输入文本长度大于512，记录索引
#                         self.long_samples.append(len(self.samples))
                    self.samples.append({
                        "id": id,
                        "context": context,
                        "question": question,
                        "answer_start": answer_start,
                        "answer_text": answer_text
                    })

    def __len__(self):
        return len(self.samples)

    def __getitem__(self, index):
        sample = self.samples[index]
        input_dict = tokenizer.encode_plus(
            sample["question"], sample["context"], max_length=512, padding="max_length", truncation=True, return_tensors="pt"
        )
        start_positions = torch.tensor(sample["answer_start"], dtype=torch.long)
        end_positions = torch.tensor([start_position + len(answer_text) - 1 for start_position, answer_text in zip(sample["answer_start"], sample["answer_text"])], dtype=torch.long)
#         if start_positions[0] >= 512: # 如果答案的起始位置超过了最大长度，则截断到最大长度-1
#             start_positions[0] = 511
#             end_positions[0] = 511
#         elif end_positions[0] >= 512: # 如果答案的结束位置超过了最大长度，则截断到最大长度-1
#             end_positions[0] = 511
#         if index in self.long_samples:  # 如果当前样本输入文本长度大于512，对标签进行特殊处理

#         print(start_positions,end_positions)
        start_positions[(start_positions >= 512) | (start_positions < 0)] = 510
        end_positions[(end_positions >= 512) | (end_positions < 0)] = 511        
        
        input_dict["start_positions"] = start_positions
        input_dict["end_positions"] = end_positions
        
        return input_dict

In [27]:
TRAIN_BATCH_SIZE = 16
path ="./CJRC/transfered/big_train_data.json"

train_dataset = MyDataset(path)

train_data_loader = torch.utils.data.DataLoader(
    train_dataset,
    batch_size=TRAIN_BATCH_SIZE,
    num_workers=0 # 这个是多线程数，最好设为0
)

len(train_data_loader)

2382

In [86]:
class BertQA(nn.Module):
    
    def __init__(self, pretrained_path, config_path):
        super(BertQA, self).__init__()
        self.config = BertConfig.from_pretrained(config_path)
        self.bert = BertModel.from_pretrained(pretrained_path, config=self.config)
#         self.bert = BertForQuestionAnswering.from_pretrained(pretrained_path, config=config)
        self.dropout = torch.nn.Dropout(self.bert.config.hidden_dropout_prob)
        self.qa_outputs = torch.nn.Linear(self.bert.config.hidden_size, 2)
        
    def forward(self, input_ids, attention_mask, token_type_ids):
        outputs = self.bert(input_ids, attention_mask=attention_mask, token_type_ids=token_type_ids)
        sequence_output = outputs[0]
        pooled_output = outputs[1]
#         print("sequence_output's shape: ",sequence_output.shape)
#         print("pooled_output's shape: ",pooled_output.shape)
        
        logits = self.qa_outputs(sequence_output)
        start_logits, end_logits = logits.split(1, dim=-1)
        start_logits = start_logits.squeeze(-1)
        end_logits = end_logits.squeeze(-1)
        return start_logits, end_logits

In [8]:
import torch.optim as optim
from tqdm import tqdm
import torch.nn.functional as F

def train_fn(model, dataloader, optimizer, device='cpu', epochs=3, scheduler=None):
#     optimizer = optim.Adam(model.parameters(), lr=learning_rate)

    model.train()
    
    criterion = torch.nn.CrossEntropyLoss()
#     loss_fct = torch.nn.NLLLoss()

    for epoch in range(epochs):
        print(f"Epoch {epoch+1}/{epochs}")
        running_loss = 0.0
        
        for data in tqdm(dataloader, desc="Training"):
            
            input_ids = data["input_ids"].squeeze(dim=1).to(device)
            attention_mask = data["attention_mask"].squeeze(dim=1).to(device)
            token_type_ids = data["token_type_ids"].squeeze(dim=1).to(device)
            start_positions = data["start_positions"].to(device)
            end_positions = data["end_positions"].to(device)
            
            optimizer.zero_grad()
            
#             input_ids = data["input_ids"].squeeze(dim=1).to(device, dtype=torch.long)
#             attention_mask = data["attention_mask"].squeeze(dim=1).to(device, dtype=torch.long)
#             token_type_ids = data["token_type_ids"].squeeze(dim=1).to(device, dtype=torch.long)
#             start_positions = data["start_positions"].to(device, dtype=torch.long)
#             end_positions = data["end_positions"].to(device, dtype=torch.long)
            
            start_logits, end_logits = model(input_ids=input_ids, attention_mask=attention_mask, token_type_ids=token_type_ids)
        
            print("start_logits's shape: ",start_logits.shape)
            print("start_positions's shape: ",start_positions.shape)
            
            start_probs = F.softmax(start_logits, dim=-1)
            end_probs = F.softmax(end_logits, dim=-1)
            
            start_positions = start_positions[:, 0]
            end_positions = end_positions[:, 0]
            
            print("handling after softmax:",start_probs.shape, start_positions.shape)
            
            loss_start = criterion(start_probs, start_positions)
            loss_end = criterion(end_probs, end_positions)
            loss = (loss_start + loss_end) / 2
            
            loss.backward()
            optimizer.step()
            if scheduler is not None:
                scheduler.step()
            running_loss += loss.item()
        print("Epoch {} loss: {:.4f}".format(epoch + 1, running_loss / len(dataloader)))
        
    print("Training finished!")

In [9]:
EPOCHS = 3
TRAIN_BATCH_SIZE = 32

In [36]:
import gc
gc.collect()

from transformers import AdamW
from transformers import get_linear_schedule_with_warmup

# device = torch.device("cuda")
device = torch.device("cpu")
print(device)

model = BertQA('chinese-bert-wwm')
model.to(device)

cpu


Some weights of the model checkpoint at chinese-bert-wwm were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


BertQA(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(21128, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=Tru

In [37]:
num_train_steps = int(len_train / TRAIN_BATCH_SIZE * EPOCHS)
param_optimizer = list(model.named_parameters())

# 这里是设置不应该添加正则化项的参数，一般是BN层的可训练参数及卷积层和全连接层的 bias
no_decay = ["bias", "LayerNorm.bias", "LayerNorm.weight"]
optimizer_parameters = [
    {'params': [p for n, p in param_optimizer if not any(nd in n for nd in no_decay)], 'weight_decay': 0.001},
    {'params': [p for n, p in param_optimizer if any(nd in n for nd in no_decay)], 'weight_decay': 0.0},
]
optimizer = AdamW(optimizer_parameters, lr=3e-5)

# 学习率变动函数，这里使用的是预热学习率
# 在预热期间，学习率从0线性增加到优化器中的初始lr。
# 在预热阶段之后创建一个schedule，使其学习率从优化器中的初始lr线性降低到0
# 这里没使用预热，直接从初始学习率开始下降
scheduler = get_linear_schedule_with_warmup(
    optimizer, 
    num_warmup_steps=0,  # The number of steps for the warmup phase.
    num_training_steps=num_train_steps # The total number of training steps
)

# Epoch 3 loss: 6.1104
train_fn(model, train_data_loader, optimizer, device=device, scheduler=scheduler)

Epoch 1/3


Training:   0%|                                                                               | 0/2382 [00:00<?, ?it/s]Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tok

sequence_output's shape:  torch.Size([16, 512, 768])
pooled_output's shape:  torch.Size([16, 768])
start_logits's shape:  torch.Size([16, 512])
start_positions's shape:  torch.Size([16, 1])
handling after softmax: torch.Size([16, 512]) torch.Size([16])


Training:   0%|                                                                    | 1/2382 [00:30<20:23:49, 30.84s/it]Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tok

sequence_output's shape:  torch.Size([16, 512, 768])
pooled_output's shape:  torch.Size([16, 768])
start_logits's shape:  torch.Size([16, 512])
start_positions's shape:  torch.Size([16, 1])
handling after softmax: torch.Size([16, 512]) torch.Size([16])


...

sequence_output's shape:  torch.Size([16, 512, 768])
pooled_output's shape:  torch.Size([16, 768])
start_logits's shape:  torch.Size([16, 512])
start_positions's shape:  torch.Size([16, 1])
handling after softmax: torch.Size([16, 512]) torch.Size([16])


Training:   0%|                                                                    | 4/2382 [02:02<20:09:02, 30.51s/it]Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tok

sequence_output's shape:  torch.Size([16, 512, 768])
pooled_output's shape:  torch.Size([16, 768])
start_logits's shape:  torch.Size([16, 512])
start_positions's shape:  torch.Size([16, 1])
handling after softmax: torch.Size([16, 512]) torch.Size([16])


Training:   0%|                                                                    | 4/2382 [02:26<24:07:51, 36.53s/it]


KeyboardInterrupt: 

In [ ]:
# 保存训练好的模型
torch.save({'state_dict': model.state_dict()}, 'self_QA/bert_model/cjrc_model_dict.pth.bar')
# tokenizer.save_pretrained('self_QA/bert_tokenizer')

In [89]:
# 目前使用的是“bert-base-chinese”预训练模型，在Kaggle上训练的

# config = BertConfig.from_pretrained('bert-base-chinese')

model = BertQA('bert-base-chinese',config_path="self_QA/config.json")
checkpoint = torch.load('self_QA/bert_model/cjrc_model_dict.pth.bar')
model.load_state_dict(checkpoint['state_dict'])

Some weights of the model checkpoint at bert-base-chinese were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


<All keys matched successfully>

In [72]:
# 验证流程
device = 'cuda'

def evaluate(model, dataloader):
    model.eval()
    criterion = torch.nn.CrossEntropyLoss()
    
    total_loss = 0.0
    for batch in tqdm(dataloader, desc="Validating"):    
        
        with torch.no_grad():
            input_ids = batch["input_ids"].squeeze(dim=1).to(device)
            attention_mask = batch["attention_mask"].squeeze(dim=1).to(device)
            token_type_ids = batch["token_type_ids"].squeeze(dim=1).to(device)
            start_positions = batch["start_positions"].to(device)
            end_positions = batch["end_positions"].to(device)
            
            start_logits, end_logits = model(input_ids=input_ids, attention_mask=attention_mask, token_type_ids=token_type_ids)
            
            print("start_logits's shape: ",start_logits.shape)
            print("start_positions's shape: ",start_positions.shape)
#             print(start_positions)
            
            start_probs = F.softmax(start_logits, dim=-1)
            end_probs = F.softmax(end_logits, dim=-1)
            
            start_positions = start_positions[:, 0]
            end_positions = end_positions[:, 0]
            
            loss_start = criterion(start_probs, start_positions)
            loss_end = criterion(end_probs, end_positions)
            loss = (loss_start + loss_end) / 2
            
            total_loss += loss.item() * input_ids.size(0)

    avg_loss = total_loss / len(dataloader)
    return avg_loss

In [73]:
# 加载验证集数据
VAL_BATCH_SIZE = 32

dev_path = "./CJRC/transfered/dev_ground_truth.json"
# dev_dataset = MyDataset(dev_path, mode='val')
dev_dataset = MyDataset(dev_path)

dev_data_loader = torch.utils.data.DataLoader(
    dev_dataset,
    batch_size=VAL_BATCH_SIZE,
    num_workers=0 # 这个是多线程数，最好设为0
)

print(len(dev_data_loader))

model.to(device)
dev_loss = evaluate(model, dev_data_loader)
print("Validation Loss:", dev_loss) # Validation Loss: 191.47054347586123

188


Validating:   0%|                                                                              | 0/188 [00:00<?, ?it/s]Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.


start_logits's shape:  torch.Size([32, 512])
start_positions's shape:  torch.Size([32, 3])


Validating:   1%|▎                                                                     | 1/188 [00:00<03:01,  1.03it/s]Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tok

start_logits's shape:  torch.Size([32, 512])
start_positions's shape:  torch.Size([32, 3])


...

start_logits's shape:  torch.Size([32, 512])
start_positions's shape:  torch.Size([32, 3])


Validating:  99%|███████████████████████████████████████████████████████████████████▋| 187/188 [02:06<00:00,  1.50it/s]Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tokens have been removed.
Be aware, overflowing tokens are not returned for the setting you have chosen, i.e. sequence pairs with the 'longest_first' truncation strategy. So the returned list will always be empty even if some tok

start_logits's shape:  torch.Size([16, 512])
start_positions's shape:  torch.Size([16, 3])


Validating: 100%|████████████████████████████████████████████████████████████████████| 188/188 [02:07<00:00,  1.48it/s]

Validation Loss: 191.47054347586123


In [99]:
# 测试用例

from transformers import pipeline
from transformers import BertTokenizer, BertConfig
import json

# 提取模型配置信息
# config_dict = model.config.to_dict()
# config_json = json.dumps(config_dict)
# config = BertConfig.from_dict(config_dict)
tokenizer = BertTokenizer.from_pretrained("bert-base-chinese")

# 定义三个问题和对应的上下文材料（非法律相关）
question_1 = "北京大学成立于何时？"
context_1 = "北京大学创立于1898年，前身为京师大学堂，是中国近现代第一所国立综合性大学..."
question_2 = "新冠肺炎爆发于哪里？"
context_2 = "2019年12月，新冠肺炎（COVID-19）爆发于中国湖北省武汉市，世界卫生组织将其公布为全球流行病"
question_3 = "新冠肺炎的病原体是什么？"
context_3 = "新冠肺炎是一种人畜共患病，病原体为新型冠状病毒。目前还没有特效药物或疫苗可供使用..."

# 法律相关问题
question_law_1 = "谁胜诉了？"
context_law_1 = '''一、被告 东营美利达新型材料科技有限公司 于本判决生效之日起十日内支付原告 山东富润润滑油股份有限公司 货款153540元、违约金23584.5及自2021年3月20日起至清偿之日止的违约金（违约金计算方式：以153540元为基数，按日万分之五计算）；\r\n二、驳回原告<a href="https://www.tianyancha.com/company/3366658716" target="_blank" data-type="company">山东富润润滑油股份有限公司</a>的其他诉讼请求。\r\n如果未按本判决指定的期间履行给付金钱义务，应当依照《中华人民共和国民事诉讼法》第二百六十条规定，加倍支付迟延履行期间的债务利息。\r\n案件受理费5357元，减半收取计2678.5元，由被告<a href="https://www.tianyancha.com/company/2339951049" target="_blank" data-type="company">东营美利达新型材料科技有限公司</a>负担，于本判决生效后七日内向本院交纳。\r\n如不服本判决，可以在判决书送达之日起十五日内，向本院递交上诉状，并按对方当事人的人数提出副本，同时按照不服本判决部分的上诉请求数额，交纳案件受理费，上诉于山东省东营市中级人民法院。上诉期满后七日内仍未交纳上诉案件受理费的，按自动撤回上诉处理。'''
question_law_2 = "如果对判决不服该怎么做？"
context_law_2 = '''被告季先启于本判决生效后十日内支付原告奇瑞徽银汽车金融股份有限公司贷款本金52907.93元，利息5631.82元，罚息6206.07元，复利943.65元，共计人民币65689.47元，并自2021年8月6日起至实际清偿之日止按合同约定的利率支付罚息（以所欠本金52907.93元为基数）、复利（以所欠利息5631.82元为基数）；\r\n二、原告奇瑞徽银汽车金融股份有限公司对抵押车辆（车牌号苏Ｂ×××**，车架号ＬＬＶ2ＡＶＢ25Ｊ0000949）的折价、拍卖、变卖所得价款享有优先受偿权。\r\n如果未按本判决指定的期间履行给付金钱义务，应当依照《中华人民共和国民事诉讼法》第二百五十三条之规定，加倍支付迟延履行期间的债务利息。\r\n案件受理费为721元，由被告季先启负担。\r\n如不服本判决，可以在判决书送达之日起十五日内，向本院递交上诉状，并按对方当事人的人数或者代表人的人数提出副本，上诉于安徽省芜湖市中级人民法院。'''
question_law_3 = "吴生祥应被赔偿多少钱？"
context_law_3 = r"一、中国平安财产保险股份有限公司无锡分公司赔偿吴生祥123742.6元，上述款项于本判决发生法律效力之日起10日内付清。\r\n二、驳回吴生祥的其他诉讼请求。\r\n如果未按本判决指定的期间履行给付金钱义务，应当依照《中华人民共和国民事诉讼法》第二百五十三条之规定，加倍支付迟延履行期间的债务利息。\r\n本案诉讼费3581元，其中案件受理费1042元减半收取计521元，鉴定费3060元。由吴生祥负担132元，由保险公司负担3449元（吴生祥同意其预交的诉讼费用中的剩余部分3449元，由被告向其直接支付，本院不再退还，保险公司在本判决生效之日起十日内向吴生祥支付）。\r\n如不服本判决，可在判决书送达之日起十五日内，向本院递交上诉状，并按对方当事人的人数提出副本，上诉于江苏省无锡市中级人民法院。同时根据《诉讼费用交纳办法》的有关规定，向该院预交上诉案件受理费。"
question_law_4 = "山东恒宇精密薄板有限公司的法定代表人是谁？"
context_law_4 = r"山东省博兴县人民法院执 行 裁 定 书（2016）鲁1625执311号申请执行人东营市富润润滑油有限公司，住所地:东营市黄河路160-3号。法定代表人：徐炳胜，该公司经理。被执行人山东恒宇精密薄板有限公司，住所地：博兴县店子镇工业园区法定代表人：魏炳涛，该公司经理。申请执行人与被执行人民间借贷纠纷一案于2016年5月5日立案执行，执行标的171796元。本院在执行过程查明被执行人无履行能力，该案暂不具备履行能力，应予以终结。依据《中华人民共和国民事诉讼法》第一百五十四条，第二百五十七条之规定，裁定如下：一、终结博兴县人民法院(2015)博商初字第848号民事判决书的本次执行程序。二、申请执行人在具备执行条件时，可以向有管辖权的人民法院申请执行该债权。三、本裁定书一经送达，即发生法律效力"
question_law_5 = "双方约定借款利率是多少？"
question_law_51 = "反担保保证方式是什么？？"
context_law_5 =r"本院经审理查明:2013年12月27日贺x16与湘潭县农村信用合作联社签订《个人贷款合同》,约定借款700万元,借款期限为12个月,贷款利率按月利率9.5‰计算,逾期罚息利率在原借款利率基础上加收40%,借款人贺x16未按照约定偿还本合同下借款本息及其他应付款项构成违约,借款人违约,贷款人有权宣布合同到期,并立即收回未偿还款项借款为保证贷款同日,湘潭县农村信用合作联社如实发放贷款当日,贺x16与原告恒宇担保签订了《委托担保合同》,合同约定,贺x16委托恒宇担保对其与湘潭县农村信用合作联社签订的《个人贷款合同》700万元借款提供担保,贺x16未履行或未完全履行本合同第六条约定义务的,恒宇担保有权要求贺x16按照本合同约定的被担保的主债权数额的10%支付违约金贺x16未按照主合同约定按期清偿债务,造成恒宇担保为贺x16向湘潭县农村信用合作联社代偿的,应按代偿数额向恒宇担保支付每日万分之十五的代偿利息担保债权的范围包括借款本金、利息、违约金、损害赔偿金、实现债权的费用(诉讼费用、律师代理费、财产保全费、公告费等)2013年12月26日,原告恒宇担保与湘潭县农村信用合作联社签订了《最高额保证合同》,约定恒宇担保为贺x16与农村信用联社之间700万元借款提供保证担保保证方式为连带责任保证,保证人的保证期间为主合同约定的债务人履行债务期限届满之日起二年若发生借款合同约定的事项,导致借款合同项下债务提前到期的,湘潭县农村信用联社有权要求恒宇担保提前履行保证责任,恒宇担保保证期间自主合同债务提前到期之日起二年恒宇担保不按本合同约定履行保证责任的,湘潭县农村信用合作联社可以直接从保证人的任何账户中划收相关款项2013年12月27日,原告恒宇担保与贺x16以及被告宏兴隆、胡x4签订《保证反担保合同》,约定:为确保恒宇担保债权的实现,贺x16以及被告宏兴隆、胡x4自愿为贺x16作为恒宇担保的反担保保证人,提供保证反担保保证方式为连带保证责任保证合同担保的范围包括主合同项下的债务本金、利息、逾期利息、罚息、复利、手续费、违约金、损害赔偿金、实现债权的费用(包括但不限于诉讼费、仲裁费、执行费、保全费、鉴定费、律师代理费、差旅费等及其他一切费用)另,贺x16向原告恒宇担保交纳了140万元保证金"

qa_pipeline = pipeline('question-answering', model=model, tokenizer=tokenizer)
# qa_pipeline = pipeline('question-answering', model=model, tokenizer=tokenizer, config="bert-base-chinese")
result1 = qa_pipeline(question=question_1, context=context_1)
print("model answer question_1: \n", result1['answer'])

result2 = qa_pipeline(question=question_2, context=context_2)
print("model answer question_2: \n", result2['answer'])

result3 = qa_pipeline(question=question_3, context=context_3)
print("model answer question_3: \n", result3['answer'])

print("\n","="*40,"Law Questions","="*40,"\n")

result_law_1 = qa_pipeline(question=question_law_1, context=context_law_1)
print("model answer law question_1: \n", result_law_1['answer'])

result_law_2 = qa_pipeline(question=question_law_2, context=context_law_2)
print("model answer law question_2: \n", result_law_2['answer'])

result_law_3 = qa_pipeline(question=question_law_3, context=context_law_3)
print("model answer law question_3: \n", result_law_3['answer'])

result_law_4 = qa_pipeline(question=question_law_4, context=context_law_4)
print("model answer law question_4: \n", result_law_4['answer'])

result_law_5 = qa_pipeline(question=question_law_5, context=context_law_5)
print("model answer law question_5: \n", result_law_5)

result_law_51 = qa_pipeline(question=question_law_51, context=context_law_5)
print("model answer law question_51: \n", result_law_51)

The model 'BertQA' is not supported for question-answering. Supported models are ['AlbertForQuestionAnswering', 'BartForQuestionAnswering', 'BertForQuestionAnswering', 'BigBirdForQuestionAnswering', 'BigBirdPegasusForQuestionAnswering', 'BloomForQuestionAnswering', 'CamembertForQuestionAnswering', 'CanineForQuestionAnswering', 'ConvBertForQuestionAnswering', 'Data2VecTextForQuestionAnswering', 'DebertaForQuestionAnswering', 'DebertaV2ForQuestionAnswering', 'DistilBertForQuestionAnswering', 'ElectraForQuestionAnswering', 'ErnieForQuestionAnswering', 'ErnieMForQuestionAnswering', 'FlaubertForQuestionAnsweringSimple', 'FNetForQuestionAnswering', 'FunnelForQuestionAnswering', 'GPT2ForQuestionAnswering', 'GPTNeoForQuestionAnswering', 'GPTNeoXForQuestionAnswering', 'GPTJForQuestionAnswering', 'IBertForQuestionAnswering', 'LayoutLMv2ForQuestionAnswering', 'LayoutLMv3ForQuestionAnswering', 'LEDForQuestionAnswering', 'LiltForQuestionAnswering', 'LongformerForQuestionAnswering', 'LukeForQuestion

model answer question_1: 
 北京大学创立于1898年，前身为京师大学堂，是中国近现代第一所国立综合性大学...
model answer question_2: 
 2019年12月，新冠肺炎（COVID-19）爆发于中国湖北省武汉市，世界卫生组织将其公布为全球流行病
model answer question_3: 
 新冠肺炎是一种人畜共患病，病原体为新型冠状病毒。目前还没有特效药物或疫苗可供使用...

 ======================================== Law Questions ======================================== 

model answer law question_1: 
 一、被告
model answer law question_2: 
 如果未按本判决指定的期间履行给付金钱义务，应当依照《中华人民共和国民事诉讼法》第二百五十三条之规定，加倍支付迟延履行期间的债务利息。
model answer law question_3: 
 一、中国平安财产保险股份有限公司无锡分公司赔偿吴生祥123742.6元，上述款项于本判决发生法律效力之日起10日内付清。\r\n二、驳回吴生祥的其他诉讼请求。\r\n如果未按本判决指定的期间履行给付金钱义务，应当依照《中华人民共和国民事诉讼法》第二百五十三条之规定，加倍支付迟延履行期间的债务利息。\r\n本案诉讼费3581元，其中案件受理费1042元减半收取计521元，鉴定费3060元。由吴生祥负担132元，由保险公司负担3449元（吴生祥同意其预交的诉讼费用中的剩余部分3449元，由被告向其直接支付，本院不再退还，保险公司在本判决生效之日起十日内向吴生祥支付）。\r\n如不服本判决，可在判决书送达之日起十五日内，向本院递交上诉状，并按对方当事人的人数提出副本，上诉于江苏省无锡市中级人民法院。同时根据《诉讼费用交纳办法》的有关规定，向该院预交上诉案件受理费。
model answer law question_4: 
 书（2016）鲁1625执311号申请执行人东营市富润润滑油有限公司，住所地:东营市黄河路160-3号。法定代表人：徐炳胜，该公司经理。被执行人山东恒宇精密薄板有限公司，住所地：博兴县店子镇工业园区法

In [100]:
qa_pipeline = pipeline('question-answering', model=model, tokenizer=tokenizer)

context = "依据上述有效证据,本院确认以下案件事实:原、被告双方于××××年××月份结婚,婚后生一女孩,取名马62,2013年11月21日,双方在新民市民政局协议离婚,协议内容为:婚生女孩马62由女方别x2抚养,男方每月给孩子抚养费1000元(从2013年12月1日起至2020年12月止)双方离婚后,小孩马62一直随被告生活××××年××月××日,婚生女孩马62从内乡县第二小学转入沈阳大学新民师范学院附属小学上学至今,现原告以小孩马62已年满十周岁,自愿提出与原告一起生活为由,诉至法院,请求依法变更小孩马62由原告抚养"
question_1 = "离婚协议约定马62由谁抚养？"
question_2 = "原、被告双方于何时离婚？"
question_3 = "马62目前在何处上学？"

res_1 = qa_pipeline(question=question_1, context=context)
print("model answer law question_1: \n", res_1)

res_2 = qa_pipeline(question=question_2, context=context)
print("model answer law question_2: \n", res_2)

res_3 = qa_pipeline(question=question_3, context=context)
print("model answer law question_3: \n", res_3)

The model 'BertQA' is not supported for question-answering. Supported models are ['AlbertForQuestionAnswering', 'BartForQuestionAnswering', 'BertForQuestionAnswering', 'BigBirdForQuestionAnswering', 'BigBirdPegasusForQuestionAnswering', 'BloomForQuestionAnswering', 'CamembertForQuestionAnswering', 'CanineForQuestionAnswering', 'ConvBertForQuestionAnswering', 'Data2VecTextForQuestionAnswering', 'DebertaForQuestionAnswering', 'DebertaV2ForQuestionAnswering', 'DistilBertForQuestionAnswering', 'ElectraForQuestionAnswering', 'ErnieForQuestionAnswering', 'ErnieMForQuestionAnswering', 'FlaubertForQuestionAnsweringSimple', 'FNetForQuestionAnswering', 'FunnelForQuestionAnswering', 'GPT2ForQuestionAnswering', 'GPTNeoForQuestionAnswering', 'GPTNeoXForQuestionAnswering', 'GPTJForQuestionAnswering', 'IBertForQuestionAnswering', 'LayoutLMv2ForQuestionAnswering', 'LayoutLMv3ForQuestionAnswering', 'LEDForQuestionAnswering', 'LiltForQuestionAnswering', 'LongformerForQuestionAnswering', 'LukeForQuestion

model answer law question_1: 
 {'score': 2.3139087090839894e-07, 'start': 0, 'end': 255, 'answer': '依据上述有效证据,本院确认以下案件事实:原、被告双方于××××年××月份结婚,婚后生一女孩,取名马62,2013年11月21日,双方在新民市民政局协议离婚,协议内容为:婚生女孩马62由女方别x2抚养,男方每月给孩子抚养费1000元(从2013年12月1日起至2020年12月止)双方离婚后,小孩马62一直随被告生活××××年××月××日,婚生女孩马62从内乡县第二小学转入沈阳大学新民师范学院附属小学上学至今,现原告以小孩马62已年满十周岁,自愿提出与原告一起生活为由,诉至法院,请求依法变更小孩马62由原告抚养'}
model answer law question_2: 
 {'score': 2.8449456294765696e-05, 'start': 0, 'end': 255, 'answer': '依据上述有效证据,本院确认以下案件事实:原、被告双方于××××年××月份结婚,婚后生一女孩,取名马62,2013年11月21日,双方在新民市民政局协议离婚,协议内容为:婚生女孩马62由女方别x2抚养,男方每月给孩子抚养费1000元(从2013年12月1日起至2020年12月止)双方离婚后,小孩马62一直随被告生活××××年××月××日,婚生女孩马62从内乡县第二小学转入沈阳大学新民师范学院附属小学上学至今,现原告以小孩马62已年满十周岁,自愿提出与原告一起生活为由,诉至法院,请求依法变更小孩马62由原告抚养'}
model answer law question_3: 
 {'score': 1.1740628025336264e-08, 'start': 0, 'end': 255, 'answer': '依据上述有效证据,本院确认以下案件事实:原、被告双方于××××年××月份结婚,婚后生一女孩,取名马62,2013年11月21日,双方在新民市民政局协议离婚,协议内容为:婚生女孩马62由女方别x2抚养,男方每月给孩子抚养费1000元(从2013年12月1日起至2020年12月止)双方离婚后,小孩马62一直随被告生活××××年××月××日,婚生女孩马62从内乡县第二

In [13]:
with open(dev_path, "r", encoding="utf-8") as f:
    data_test = json.load(f)["data"]
    
data_test

[{'title': 'civil-1',
  'paragraphs': [{'context': '经审理查明:原告曹0与被告张x1原5夫妻关系2001年5月27日,原、被告生育一女张x62011年7月21日,原、被告因夫妻感情破裂,在重庆市荣昌县人民法院调解离婚,调解书载明:“原、被告之女张x6随被告张x1生活”原、被告离婚后又自行协商,约定小孩张x6暂由原告代管,被告每月向原告支付张x6的生活费800元因此,张x6一直随原告生活至今,期间被告未依照约定按时向原告支付张x6的生活费另查明:张x6现在荣昌县城西小学上学,为城镇居民户口原告曹0系重庆博耐特压铸有限公司职工,收入比较稳定,现已再婚,其与丈夫何祖君共同购买了位于荣昌县昌元街道昌州大道西段的房屋一套本案在审理过程中,本院依法对张x6作了询问笔录,张x6称从父母离婚后其一直随母亲生活,只在每年暑假到父亲家里玩耍一段时间,现在自己愿意随母亲曹0生活上述事实,有原告陈述,被告答辩状,常住人口登记卡,重庆市荣昌县人民法院作出的(2011)荣4民初字第1929号民事调解书,原、被告签订的协议,结婚证,房产证,劳动合同,重庆市基本养老保险个人账户信息表,对张x6的询问笔录等证据予以证实',
    'qas': [{'id': '1_1',
      'question': '原告曹0与被告张x1因何离婚？',
      'answers': [{'answer_start': 60, 'text': '夫妻感情破裂'},
       {'answer_start': 59, 'text': '因夫妻感情破裂'},
       {'answer_start': 60, 'text': '夫妻感情破裂'}],
      'is_impossible': 'false'},
     {'id': '1_2',
      'question': '双方约定被告每月支付多少生活费？',
      'answers': [{'answer_start': 151, 'text': '800元'},
       {'answer_start': 148, 'text': '生活费800元'},
       {'answer_start': 151, 'text': '800元'}],
      'is_i

In [33]:
weights = torch.tensor([0.2,0.7,0.07])
unsqueezed_weights = weights.unsqueeze(1)
unsqueezed_weights

tensor([[0.2000],
        [0.7000],
        [0.0700]])

In [38]:
unsqueezed_weights[unsqueezed_weights >= 0.1 or unsqueezed_weights < 0] = 0.1
unsqueezed_weights

tensor([[0.1000],
        [0.1000],
        [0.0700]])

In [37]:
test_t = torch.tensor([[0,0.05],[0.1,1]])
print(test_t)
test_t[test_t >= 0.1] = 0.1
test_t

tensor([[0.0000, 0.0500],
        [0.1000, 1.0000]])


tensor([[0.0000, 0.0500],
        [0.1000, 0.1000]])

In [59]:
test_t = torch.tensor([60, 59, 60], device='cuda:0')
print(test_t.size())
print(test_t.shape)
test_t.unsqueeze_(0)
print(test_t.size())
print(test_t.shape)

torch.Size([3])
torch.Size([3])
torch.Size([1, 3])
torch.Size([1, 3])
